In [1]:
#!pip3 install --upgrade tensorflow-gpu

#!pip3 install tensorflow-hub

In [1]:
#importing the modules
import tensorflow as tf
import tensorflow_hub as hub
import numpy as np
import pandas as pd

In [2]:
#creating the model
module_url = "https://tfhub.dev/google/universal-sentence-encoder/4" 
model = hub.load(module_url)

In [3]:
#read data
data = pd.read_csv(r"Text_Similarity_Dataset.csv")
data.shape

(4023, 3)

In [4]:
#Sentences are encoded to vector quantities
#list of vectors of all the sentences in both text1 and text2 are created respectively
list_sent1 = []
for i in range(4023):
    sentence1 = data['text1'].iloc[i]
    sent1_vec = model([sentence1])[0]
    list_sent1.append(sent1_vec)

list_sent2 = []
for i in range(4023):
    sentence2 = data['text2'].iloc[i]
    sent2_vec = model([sentence2])[0]
    list_sent2.append(sent2_vec)

In [5]:
len(list_sent2)

4023

In [6]:
list_sent2

[<tf.Tensor: shape=(512,), dtype=float32, numpy=
 array([-4.06474248e-02, -5.54491058e-02, -5.75323030e-02, -4.56275530e-02,
         5.81513196e-02, -1.02916993e-02,  5.06252348e-02,  1.61099639e-02,
         3.88863832e-02,  5.83816953e-02, -5.86062521e-02,  4.95124795e-02,
        -5.41972518e-02, -5.54437041e-02,  1.13584148e-02, -2.52914317e-02,
         4.90648374e-02,  3.67740318e-02, -9.33454465e-03,  1.96825508e-02,
        -5.41722924e-02,  4.63950969e-02, -2.77312249e-02, -3.58667620e-03,
        -2.71166023e-02,  3.70472320e-03,  3.91776413e-02,  3.04066185e-02,
        -5.33378832e-02,  2.07288992e-02, -4.20519337e-02,  5.70174456e-02,
         2.51520220e-02,  4.88206856e-02, -2.89487792e-03, -4.67015132e-02,
         5.30733988e-02,  5.67891635e-02, -5.78432269e-02, -4.92913797e-02,
        -5.86060658e-02,  1.22732911e-02, -5.32324612e-02, -4.68524732e-02,
        -5.86062521e-02, -5.77102825e-02, -4.69123535e-02,  1.26580177e-02,
         3.08108814e-02,  1.87770650e-0

In [7]:
#cosine function
def cosine(u, v):
    return np.dot(u, v) / (np.linalg.norm(u) * np.linalg.norm(v))

In [8]:
#computing similarity score using cosine and appending it in a list 
sim_score_arr = []
for i in range(4023):
    similarity_score = cosine(list_sent1[i], list_sent2[i])
    sim_score_arr.append(similarity_score)

In [9]:
len(sim_score_arr)

4023

In [11]:
#check for any negative value
for i in range(4023):
    if sim_score_arr[i] < 0:
        print(i,sim_score_arr[i])

3691 -0.01641213


In [23]:
#as you can see that at index 3691 our model is returning a value that is less thn 0
#now we will convert it to lie in the range [0,1] using cosine distance
norm_similarity_score = []
for i in range(4023):
    cosine_distance = (1 - sim_score_arr[i])
    norm_cosine_distance = cosine_distance/2
    norm_similarity_score.append(norm_cosine_distance)


In [24]:
len(norm_similarity_score)

4023

In [25]:
#check for any negative value
for i in range(4023):
    if norm_similarity_score[i] < 0:
        print(i,norm_similarity_score[i])
    else: 
        exit()

#now there are no negative values since all of our values lies in range [0,1]

In [ ]:
#creating submission csv
sim_score_df = pd.DataFrame(norm_similarity_score)
submission_df = pd.DataFrame()
submission_df['Unique_ID'] = data['Unique_ID']
submission_df['Similarity_Score'] = sim_score_df
final_submission = submission_df.to_csv(r'final_submission.csv',index=False) 